In [ ]:
#Demonstrates k Nearest Neighbors

#Import packages
import numpy as np
import pandas as pd
import math
import geopandas as gpd
import matplotlib.pyplot as plt

In [22]:
#Load data
block_shape = gpd.read_file("allegheny_county_census_block_groups_2016.zip")
train_data = pd.read_csv("training_data.csv")
test_data = pd.read_csv("testing_data.csv")
del train_data["Unnamed: 0"]
del test_data["Unnamed: 0"]
all_data = pd.concat([train_data,test_data], ignore_index = True)

In [38]:
#Applying KNN for our predictions
geoid_list = []
prediction_val = []
groups_predicted = []
geometry_predicted = []
for geo in all_data["geoid"]:
    if geo not in geoid_list:
        geoid_list.append(geo)
for geo_id in geoid_list:
    id_map_test = all_data.drop(all_data[all_data['geoid'] != geo_id].index)
    id_map_test.reset_index(inplace = True)
    del id_map_test["index"]
    if len(id_map_test["geoid"]) >= 20:
        total_num = len(id_map_test["geoid"])
        neighbor_num = int(math.ceil(math.sqrt(len(id_map_test["geoid"]))))
        comp_nums = []
        for j in range(total_num - neighbor_num, total_num):
            comp_nums.append(id_map_test["counts"][j])
        prediction = math.ceil(sum(comp_nums)/len(comp_nums))
        prediction_val.append(prediction)
        #Commented out as to not create a bunch of graphs (for now)
        #plt.scatter(id_map_test["year_quarter"], id_map_test["counts"], color = "red", label = "Past Data")
        #plt.scatter("2024 Q4", prediction, color = "blue", label = "Predicted Quarter 4 2024 Value")
        #plt.plot(id_map_test["year_quarter"], id_map_test["counts"], color = "red")
        #plt.xlabel('Time')
        #plt.ylabel('Number of OD EMS Calls')
        #plt.title("Geoid: " + str(id_map_test["geoid"][0]))
        #plt.xticks(rotation=90)
        #plt.legend(loc="upper left")
        #plt.show()
        print("KNN Prediction:",prediction,"for census block group:",geo_id)
        groups_predicted.append(geo_id)
        geometry_predicted.append(id_map_test["geometry"][0])

KNN Prediction: 20 for census block group: 420030103001
KNN Prediction: 5 for census block group: 420030103002
KNN Prediction: 3 for census block group: 420030103003
KNN Prediction: 2 for census block group: 420030103004
KNN Prediction: 42 for census block group: 420030201001
KNN Prediction: 13 for census block group: 420030201002
KNN Prediction: 65 for census block group: 420030201003
KNN Prediction: 3 for census block group: 420030201004
KNN Prediction: 14 for census block group: 420030201005
KNN Prediction: 23 for census block group: 420030201006
KNN Prediction: 6 for census block group: 420030203001
KNN Prediction: 3 for census block group: 420030305001
KNN Prediction: 7 for census block group: 420030305002
KNN Prediction: 2 for census block group: 420030402001
KNN Prediction: 2 for census block group: 420030402002
KNN Prediction: 2 for census block group: 420030404002
KNN Prediction: 5 for census block group: 420030405001
KNN Prediction: 4 for census block group: 420030405002
KNN 

In [41]:
#More Maps
q4_2024 = pd.DataFrame({'Geoid': groups_predicted, 'Geometry': geometry_predicted, 'Predicted Calls': prediction_val})
q4_2024['geometry'] = gpd.GeoSeries.from_wkt(q4_2024['Geometry'])
q4_2024 = gpd.GeoDataFrame(q4_2024, crs="EPSG:4326")

In [66]:
q4_2024.explore(
    column = 'Predicted Calls',
    tooltip = ['Geoid','Predicted Calls'],
    tiles = 'CartoDB positron',
    cmap = "gnuplot2_r",
    style_kwds=dict(color="black")
)